In [1]:
import tensorflow as tf

X = tf.range(10)
dataset = tf.data.Dataset.from_tensor_slices(X)
dataset

2025-10-24 16:59:53.825001: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
W0000 00:00:1761335997.286008     662 gpu_device.cc:2342] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


<_TensorSliceDataset element_spec=TensorSpec(shape=(), dtype=tf.int32, name=None)>

In [2]:
# Above is roughly the same as (above items are int32 and this are int64, but the sequence number are the same):
dataset_2 = tf.data.Dataset.range(10)
dataset_2

<_RangeDataset element_spec=TensorSpec(shape=(), dtype=tf.int64, name=None)>

In [3]:
for item in dataset:
    print(item)

tf.Tensor(0, shape=(), dtype=int32)
tf.Tensor(1, shape=(), dtype=int32)
tf.Tensor(2, shape=(), dtype=int32)
tf.Tensor(3, shape=(), dtype=int32)
tf.Tensor(4, shape=(), dtype=int32)
tf.Tensor(5, shape=(), dtype=int32)
tf.Tensor(6, shape=(), dtype=int32)
tf.Tensor(7, shape=(), dtype=int32)
tf.Tensor(8, shape=(), dtype=int32)
tf.Tensor(9, shape=(), dtype=int32)


2025-10-24 16:59:57.324863: I tensorflow/core/framework/local_rendezvous.cc:407] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


In [4]:
for item in dataset_2:
    print(item)

tf.Tensor(0, shape=(), dtype=int64)
tf.Tensor(1, shape=(), dtype=int64)
tf.Tensor(2, shape=(), dtype=int64)
tf.Tensor(3, shape=(), dtype=int64)
tf.Tensor(4, shape=(), dtype=int64)
tf.Tensor(5, shape=(), dtype=int64)
tf.Tensor(6, shape=(), dtype=int64)
tf.Tensor(7, shape=(), dtype=int64)
tf.Tensor(8, shape=(), dtype=int64)
tf.Tensor(9, shape=(), dtype=int64)


2025-10-24 16:59:57.333974: I tensorflow/core/framework/local_rendezvous.cc:407] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


In [5]:
X_nested = {
    "a": ([1, 2, 3], [4, 5, 6]),
    "b": [7, 8, 9],
}
dataset = tf.data.Dataset.from_tensor_slices(X_nested)
for item in dataset:
    print(item)

{'a': (<tf.Tensor: shape=(), dtype=int32, numpy=1>, <tf.Tensor: shape=(), dtype=int32, numpy=4>), 'b': <tf.Tensor: shape=(), dtype=int32, numpy=7>}
{'a': (<tf.Tensor: shape=(), dtype=int32, numpy=2>, <tf.Tensor: shape=(), dtype=int32, numpy=5>), 'b': <tf.Tensor: shape=(), dtype=int32, numpy=8>}
{'a': (<tf.Tensor: shape=(), dtype=int32, numpy=3>, <tf.Tensor: shape=(), dtype=int32, numpy=6>), 'b': <tf.Tensor: shape=(), dtype=int32, numpy=9>}


# Transformations

In [6]:
# For individual items in each tensor (no batches)
dataset = tf.data.Dataset.from_tensor_slices([1, 2, 3])
dataset = dataset.filter(lambda x: x < 3)
for item in dataset:
    print(item)

tf.Tensor(1, shape=(), dtype=int32)
tf.Tensor(2, shape=(), dtype=int32)


2025-10-24 16:59:57.367849: I tensorflow/core/framework/local_rendezvous.cc:407] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


In [7]:
dataset = tf.data.Dataset.from_tensor_slices(tf.range(10))
dataset = dataset.repeat(3).batch(7)
for item in dataset:
    print(item)

tf.Tensor([0 1 2 3 4 5 6], shape=(7,), dtype=int32)
tf.Tensor([7 8 9 0 1 2 3], shape=(7,), dtype=int32)
tf.Tensor([4 5 6 7 8 9 0], shape=(7,), dtype=int32)
tf.Tensor([1 2 3 4 5 6 7], shape=(7,), dtype=int32)
tf.Tensor([8 9], shape=(2,), dtype=int32)


In [8]:
dataset = dataset.map(lambda x: x * 2, num_parallel_calls=tf.data.AUTOTUNE)
for item in dataset:
    print(item)

tf.Tensor([ 0  2  4  6  8 10 12], shape=(7,), dtype=int32)
tf.Tensor([14 16 18  0  2  4  6], shape=(7,), dtype=int32)
tf.Tensor([ 8 10 12 14 16 18  0], shape=(7,), dtype=int32)
tf.Tensor([ 2  4  6  8 10 12 14], shape=(7,), dtype=int32)
tf.Tensor([16 18], shape=(2,), dtype=int32)


In [9]:
dataset = dataset.filter(lambda x: tf.reduce_sum(x) > 50)
for item in dataset:
    print(item)

tf.Tensor([14 16 18  0  2  4  6], shape=(7,), dtype=int32)
tf.Tensor([ 8 10 12 14 16 18  0], shape=(7,), dtype=int32)
tf.Tensor([ 2  4  6  8 10 12 14], shape=(7,), dtype=int32)


In [10]:
for item in dataset.take(2):
    print(item)

tf.Tensor([14 16 18  0  2  4  6], shape=(7,), dtype=int32)
tf.Tensor([ 8 10 12 14 16 18  0], shape=(7,), dtype=int32)


2025-10-24 16:59:57.439899: I tensorflow/core/framework/local_rendezvous.cc:407] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


# Shuffling data

In [11]:
dataset = tf.data.Dataset.range(10).repeat(2)
dataset = dataset.shuffle(buffer_size=10, seed=42).batch(7) # Batch before the shuffle will shuffle the entire batch against others (not useful at all).
for item in dataset:
    print(item)

tf.Tensor([5 2 8 1 7 9 2], shape=(7,), dtype=int64)
tf.Tensor([0 0 4 6 9 3 5], shape=(7,), dtype=int64)
tf.Tensor([3 8 4 1 7 6], shape=(6,), dtype=int64)


# Interleaving lines from multiple files

In [12]:
from sklearn.datasets import fetch_california_housing
import numpy as np
import pandas as pd

df = fetch_california_housing()
housing = np.c_[df.data, df.target]
# housing = housing.data
housing = pd.DataFrame(housing)
housing.columns = df.feature_names + df.target_names
housing

MedInc  HouseAge  AveRooms  AveBedrms  Population  AveOccup  Latitude  \
0      8.3252      41.0  6.984127   1.023810       322.0  2.555556     37.88   
1      8.3014      21.0  6.238137   0.971880      2401.0  2.109842     37.86   
2      7.2574      52.0  8.288136   1.073446       496.0  2.802260     37.85   
3      5.6431      52.0  5.817352   1.073059       558.0  2.547945     37.85   
4      3.8462      52.0  6.281853   1.081081       565.0  2.181467     37.85   
...       ...       ...       ...        ...         ...       ...       ...   
20635  1.5603      25.0  5.045455   1.133333       845.0  2.560606     39.48   
20636  2.5568      18.0  6.114035   1.315789       356.0  3.122807     39.49   
20637  1.7000      17.0  5.205543   1.120092      1007.0  2.325635     39.43   
20638  1.8672      18.0  5.329513   1.171920       741.0  2.123209     39.43   
20639  2.3886      16.0  5.254717   1.162264      1387.0  2.616981     39.37   

       Longitude  MedHouseVal  
0        -122.23        4.526  
1        -122.22        3.585  
2        -122.24        3.521  
3        -122.25        3.413  
4        -122.25        3.422  
...          ...          ...  
20635    -121.09        0.781  
20636    -121.21        0.771  
20637    -121.22        0.923  
20638    -121.32        0.847  
20639    -121.24        0.894  

[20640 rows x 9 columns]

In [13]:
# Separate the dataset into smaller CSVs

import math

batch_size = 5_000
batches = math.ceil(housing.shape[0] / batch_size)
start = 0
for batch in range(batches):
    batch += 1
    end = (batch * batch_size)
    filename = f"datasets/housing/housing_{batch}.csv"
    housing[start:end].to_csv(filename, index=False)
    
    start = end

In [14]:
train_filepaths = [
    "datasets/housing/housing_1.csv",
    "datasets/housing/housing_2.csv",
    "datasets/housing/housing_3.csv",
]

valid_filepaths = [
    "datasets/housing/housing_4.csv",
]

# The smaller datasets is for the test set
test_filepaths = [
    "datasets/housing/housing_5.csv",
]

In [15]:
filepath_dataset = tf.data.Dataset.list_files(train_filepaths, seed=42)
filepath_dataset

<_ShuffleDataset element_spec=TensorSpec(shape=(), dtype=tf.string, name=None)>

In [16]:
n_readers = 4 # read 4 files at a time
dataset = filepath_dataset.interleave(
    lambda filepath: tf.data.TextLineDataset(filepath).skip(1), # Skip header
    cycle_length=n_readers
)

In [17]:
count = 0
for item in dataset:
    count += 1
count

15000

In [18]:
for item in dataset:
    print(item)

tf.Tensor(b'8.3252,41.0,6.984126984126984,1.0238095238095237,322.0,2.5555555555555554,37.88,-122.23,4.526', shape=(), dtype=string)
tf.Tensor(b'4.2031,13.0,6.811111111111111,1.0185185185185186,752.0,2.785185185185185,39.02,-121.08,2.096', shape=(), dtype=string)
tf.Tensor(b'1.7159,49.0,4.491735537190083,0.993801652892562,1861.0,3.8450413223140494,33.99,-118.28,0.95', shape=(), dtype=string)
tf.Tensor(b'8.3014,21.0,6.238137082601054,0.9718804920913884,2401.0,2.109841827768014,37.86,-122.22,3.585', shape=(), dtype=string)
tf.Tensor(b'3.6087,10.0,6.317073170731708,1.083623693379791,827.0,2.8815331010452963,39.05,-121.07,1.821', shape=(), dtype=string)
tf.Tensor(b'1.7849,46.0,4.294326241134752,1.1382978723404256,1153.0,4.088652482269503,33.99,-118.28,0.993', shape=(), dtype=string)
tf.Tensor(b'7.2574,52.0,8.288135593220339,1.073446327683616,496.0,2.8022598870056497,37.85,-122.24,3.521', shape=(), dtype=string)
tf.Tensor(b'4.5042,9.0,7.129129129129129,1.117117117117117,884.0,2.6546546546546

In [19]:
housing[["MedInc", "HouseAge", "AveRooms", "AveBedrms", "Population", "AveOccup", "Latitude", "Longitude"]]

MedInc  HouseAge  AveRooms  AveBedrms  Population  AveOccup  Latitude  \
0      8.3252      41.0  6.984127   1.023810       322.0  2.555556     37.88   
1      8.3014      21.0  6.238137   0.971880      2401.0  2.109842     37.86   
2      7.2574      52.0  8.288136   1.073446       496.0  2.802260     37.85   
3      5.6431      52.0  5.817352   1.073059       558.0  2.547945     37.85   
4      3.8462      52.0  6.281853   1.081081       565.0  2.181467     37.85   
...       ...       ...       ...        ...         ...       ...       ...   
20635  1.5603      25.0  5.045455   1.133333       845.0  2.560606     39.48   
20636  2.5568      18.0  6.114035   1.315789       356.0  3.122807     39.49   
20637  1.7000      17.0  5.205543   1.120092      1007.0  2.325635     39.43   
20638  1.8672      18.0  5.329513   1.171920       741.0  2.123209     39.43   
20639  2.3886      16.0  5.254717   1.162264      1387.0  2.616981     39.37   

       Longitude  
0        -122.23  
1        -122.22  
2        -122.24  
3        -122.25  
4        -122.25  
...          ...  
20635    -121.09  
20636    -121.21  
20637    -121.22  
20638    -121.32  
20639    -121.24  

[20640 rows x 8 columns]

In [20]:
# Preprocess the data
from sklearn.preprocessing import StandardScaler
import numpy as np

# Here is sort of "hardcoded" the mean and standard deviation because we can have the entire dataset in memory
housing_num = housing[["MedInc", "HouseAge", "AveRooms", "AveBedrms", "Population", "AveOccup", "Latitude", "Longitude"]]

standard_scaler = StandardScaler()
standard_scaler.fit(housing_num)


X_mean = standard_scaler.mean_
X_std = standard_scaler.scale_
n_inputs = 8

def parse_csv_line(line):
    defaults = [0.] * n_inputs + [tf.constant([], dtype=tf.float32)] # 8 default 0s plus an empty value (output) = 9 columns
    fields = tf.io.decode_csv(line, record_defaults=defaults) # Array of tensor where each value corresponds to each csv value

    return tf.stack(fields[:-1]), tf.stack(fields[-1:]) # Group in a tensor with array of values

def preprocess(line):
    X, y = parse_csv_line(line)

    return (X - X_mean) / X_std, y

In [21]:
preprocess(b'8.32,41.0,6.91,1.02,3.0,2.5,37.88,-12.23,4.526')

(<tf.Tensor: shape=(8,), dtype=float32, numpy=
 array([ 2.3420281 ,  0.9821427 ,  0.5985983 , -0.16179633, -1.2561225 ,
        -0.05494572,  1.0525482 , 53.57654   ], dtype=float32)>,
 <tf.Tensor: shape=(1,), dtype=float32, numpy=array([4.526], dtype=float32)>)

In [22]:
# Group every above functions into one
def csv_reader_dataset(filepaths, n_readers=5, 
                       n_read_threads=tf.data.AUTOTUNE, n_parse_threads=tf.data.AUTOTUNE, 
                       shuffle_buffer_size=10_000, seed=42, batch_size=32):
    
    dataset = tf.data.Dataset.list_files(filepaths, seed=seed)
    dataset = dataset.interleave(
        lambda filepath: tf.data.TextLineDataset(filepath).skip(1),
        cycle_length=n_readers, num_parallel_calls=n_read_threads
    )
    dataset = dataset.map(preprocess, num_parallel_calls=n_parse_threads)
    dataset = dataset.shuffle(shuffle_buffer_size, seed=seed)

    return dataset.batch(batch_size).prefetch(1)

In [23]:
train_set = csv_reader_dataset(train_filepaths)
valid_set = csv_reader_dataset(valid_filepaths)
test_set = csv_reader_dataset(test_filepaths)
for item in train_set:
    print(item)

(<tf.Tensor: shape=(32, 8), dtype=float32, numpy=
array([[ 1.41923523e+00,  1.14105880e+00, -1.51053518e-01,
        -1.82791680e-01, -7.99584031e-01, -4.40591946e-02,
        -7.49971092e-01,  5.83833456e-01],
       [-1.74742162e-01, -6.86477005e-01, -6.02962971e-01,
        -1.38694495e-02,  3.02668524e+00,  2.32984442e-02,
        -8.90426755e-01,  8.68337810e-01],
       [ 1.36136636e-01, -2.03726435e+00, -8.40083510e-02,
        -1.70182750e-01, -3.71303260e-01,  1.44908112e-02,
        -1.29306746e+00,  1.98140097e+00],
       [ 1.19457734e+00, -4.48102742e-01,  3.54389429e-01,
        -1.74331054e-01,  2.38003403e-01, -8.83366540e-03,
        -9.46608603e-01,  9.48200583e-01],
       [-4.22402978e-01, -1.16322541e+00,  2.58958526e-02,
         5.08902855e-02,  9.22996402e-02, -3.94309685e-03,
        -8.90426755e-01,  1.66195762e+00],
       [-1.05516183e+00,  7.43768454e-01, -7.88807452e-01,
        -2.51686394e-01, -1.84095994e-01,  3.53557803e-02,
        -7.78061152e-01,  6

In [24]:
model = tf.keras.Sequential([
    tf.keras.layers.Dense(30, activation="relu", kernel_initializer="he_normal", input_shape=housing_num.shape[1:]),
    tf.keras.layers.Dense(1),
])
model.compile(loss="mse", optimizer="sgd")
model.fit(train_set, validation_data=valid_set, epochs=5)

Epoch 1/5


/home/julio/.local/lib/python3.10/site-packages/keras/src/layers/core/dense.py:92: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


    466/Unknown 1s 865us/step - loss: 1.6308

/home/julio/.local/lib/python3.10/site-packages/keras/src/trainers/epoch_iterator.py:164: UserWarning: Your input ran out of data; interrupting training. Make sure that your dataset or generator can generate at least `steps_per_epoch * epochs` batches. You may need to use the `.repeat()` function when building your dataset.
  self._interrupted_warning()


469/469 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.3752 - val_loss: 1.3404
Epoch 2/5
469/469 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 0.5972 - val_loss: 7.4030
Epoch 3/5
  1/469 ━━━━━━━━━━━━━━━━━━━━ 1:14 160ms/step - loss: 0.9438

2025-10-24 17:00:02.153838: I tensorflow/core/framework/local_rendezvous.cc:407] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
	 [[{{node IteratorGetNext}}]]


469/469 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.0086 - val_loss: 1.3352
Epoch 4/5
469/469 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 0.4853 - val_loss: 0.6274
Epoch 5/5
469/469 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 0.4061 - val_loss: 0.6399


In [25]:
test_mse = model.evaluate(test_set)

20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 708us/step - loss: 0.4346


In [26]:
new_set = test_set.take(3) # Pretend we have 3 new samples. As the dataset is batched, this take the first 3 batches (of 32 items each), so 32x3 = 96
y_pred = model.predict(new_set)
y_pred.shape

3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step


(96, 1)

In [27]:
first_element = []
for item in test_set.take(1):
    first_element = item[0].numpy()[0]

y_pred = model.predict(tf.convert_to_tensor([first_element]))
y_pred

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step


array([[0.4585811]], dtype=float32)

# TFRecord format

In [28]:
with tf.io.TFRecordWriter("datasets/my_data.tfrecord") as f:
    f.write(b"This is the first record")
    f.write(b"And this is the second record")

In [29]:
filepaths = ["datasets/my_data.tfrecord"]
dataset = tf.data.TFRecordDataset(filepaths)
for item in dataset:
    print(item)

tf.Tensor(b'This is the first record', shape=(), dtype=string)
tf.Tensor(b'And this is the second record', shape=(), dtype=string)


2025-10-24 17:00:04.550602: I tensorflow/core/kernels/data/tf_record_dataset_op.cc:390] TFRecordDataset `buffer_size` is unspecified, default to 262144


In [30]:
options = tf.io.TFRecordOptions(compression_type="GZIP")
with tf.io.TFRecordWriter("datasets/my_compressed.tfrecord", options) as f:
    f.write(b"Compress, compress, compress!")

In [31]:
dataset = tf.data.TFRecordDataset(["datasets/my_compressed.tfrecord"], compression_type="GZIP")
for item in dataset:
    print(item)

tf.Tensor(b'Compress, compress, compress!', shape=(), dtype=string)


# Keras preprocessing layers

In [38]:
norm_layer = tf.keras.layers.Normalization()
model = tf.keras.models.Sequential([
    norm_layer,
    tf.keras.layers.Dense(1)
])
model.compile(loss="mse", optimizer=tf.keras.optimizers.SGD(learning_rate=2e-3))
norm_layer.adapt(housing) # computes the mean and variance of every feature
model.fit(X_train, y_train, validation_data=(X_valid, y_valid), epochs=5)

UnboundLocalError: local variable 'input_shape' referenced before assignment